In [ ]:
import IPython
IPython.Application.instance().kernel.do_shutdown(True) #automatically restarts kernel

In [7]:
# deleting a column, reordering and then saving
import pandas as pd
import Utils.Reader as Reader

import scipy.sparse as sps
df = pd.read_csv(filepath_or_buffer='../data/rewatches.csv',
                         sep=",",
                         skiprows=1,
                         header=None,
                         dtype={0: int, 1: int,2: int},
                         engine='python')

Reader.df_col_normalize(df,2)
matrix_df=df.sort_values(by=[0,1])
matrix_df.to_csv('../output/out_2.csv', index=False)

In [1]:
# normalizing a column, reordering and then saving
import pandas as pd
import Utils.Reader as Reader

import scipy.sparse as sps
df = pd.read_csv(filepath_or_buffer='../data/rewatches.csv',
                 sep=",",
                 skiprows=1,
                 header=None,
                 dtype={0: int, 1: int,2: int},
                 engine='python')

df[2]= Reader.df_col_normalize(df,2)
df=df.sort_values(by=[0,1])
df.to_csv('../output/out_2.csv', index=False)

In [6]:
# normalizing a column with substitution, reordering and then saving
import pandas as pd
import Utils.Reader as Reader

import scipy.sparse as sps
matrix_df = pd.read_csv(filepath_or_buffer='../output/extended.csv',
                        sep=",",
                        skiprows=1,
                        header=None,
                        dtype={0: int, 1: int, 2: int},
                        engine='python')
matrix_df.columns = ["a","b","data"]
Reader.df_col_normalize(matrix_df,"data",{-1:-0.5,0:0.5})
matrix_df.head()

a  b  data
0  0  0  -0.5
1  0  1  -0.5
2  0  2  -0.5
3  0  3  -0.5
4  0  4  -0.5

In [2]:
# 1 HOT ENCODER
import Utils.Reader as Reader
Reader.oneHotEncoder(name="Type", colsToDelete=["Data"],colstoOneHot=["Type"],dfPath='../data/data_ICM_length.csv')

In [2]:
# DF SPLITTER
import Utils.Reader as Reader
Reader.df_splitter("Rewatch",[0,10,20],dtype={0: int, 1: int},name="rewatches_total_",dfPath='../data/rewatches/rewatches_total.csv',colstoDefine=["UserID","Rewatch"])

In [2]:
# DF PREPROCESSING MODE
# 1-> Displayed (counts times a given Item has been displayed(in impressions list) to the user
# 2-> Extended (adds an interaction (-1) if a User has an item in impression list
# 3-> Count rewatches of each User-Item pair
# 4-> Count all rewatches of each user
import Utils.Reader as Reader
Reader.read_train_csr(preprocess=4,saving=True)

FileNotFoundError: [Errno 2] No such file or directory: '../data/interactions_and_impressions.csv'

In [1]:
import Utils.Reader as Reader

#READING
URM = Reader.only_read_train_csr(matrix_path="data/interactions_and_impressions.csv",matrix_format="...")
ICM =Reader.read_ICM_type(matrix_path="data/data_ICM_type.csv",matrix_format="...")
n_users, n_items , n_features=Reader.factorization(URM,ICM)
import numpy as np
import scipy.sparse as sps

#CSR CREATION
URM_csr = sps.csr_matrix((URM["Data"].values,
                          (URM["UserID"].values, URM["ItemID"].values)),
                         shape = (n_users, n_items)) #always support a desired shape


ICM_csr = sps.csr_matrix((np.ones(len(ICM["ItemID"].values)),
                          (ICM["ItemID"].values, ICM["FeatureID"].values)),
                         shape = (n_items, n_features))

ICM_csr.data = np.ones_like(ICM_csr.data) #transfor array with all 1s if xisting val


# STACKING
# N_User * N_Item
stacked_URM = sps.vstack([URM_csr, ICM_csr.T])
stacked_URM = sps.csr_matrix(stacked_URM)

# N_item * N_User
stacked_ICM = sps.csr_matrix(stacked_URM.T)


from Recommenders.KNN.ItemKNNCBFRecommender import ItemKNNCBFRecommender
from Data_manager.split_functions.split_train_validation_random_holdout import \
    split_train_in_two_percentage_global_sample
from Utils.Evaluator import EvaluatorHoldout
from Recommenders.KNN.ItemKNNCFRecommender import ItemKNNCFRecommender


Unique UserID in the URM are 41629
Unique UserID in the URM and ICM are 41629
Unique ItemID in the URM are 24507
Unique ItemID in the URM and ICM are 27968
Unique FeatureID in the URM are 5


In [9]:
URM_csr

<41629x27968 sparse matrix of type '<class 'numpy.int64'>'
	with 1554640 stored elements in Compressed Sparse Row format>

In [10]:
stacked_URM

<41634x27968 sparse matrix of type '<class 'numpy.float64'>'
	with 1577731 stored elements in Compressed Sparse Row format>

In [2]:
import Utils.Writer as Reader
from Utils.Writer import NameRecommender

submit= Reader.Writer(NameRecommender=NameRecommender.USER_ITEM, URM=URM_csr)
submit.makeSubmission()

<frozen importlib._bootstrap>:219: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject


ITEMCFCBF_ITEMKNNCF: URM Detected 3461 (12.4%) items with no interactions.
ItemKNNCFRecommender: URM Detected 3461 (12.4%) items with no interactions.
UserKNNCFRecommender: URM Detected 3461 (12.4%) items with no interactions.
Similarity column 27968 (100.0%), 2715.03 column/sec. Elapsed time 10.30 sec
Similarity column 41629 (100.0%), 1145.64 column/sec. Elapsed time 36.34 sec
[    0     1     2 ... 41626 41627 41628]
[[-0.6585771 12.710396  20.816397  ... -0.6585771 -0.6585771 -0.6585771]]
[[-0.06584095 59.995102   10.536214   ... -0.06584095 -0.06584095
  -0.06584095]]
[[-0.44292566  8.549109    3.9557273  ... -0.44292566 -0.44292566
  -0.44292566]]
[[-0.11212347 -0.11212347 -0.11212347 ... -0.11212347 -0.11212347
  -0.11212347]]
[[ 0.5577886  13.507398   12.301094   ... -0.74951035 -0.74951035
  -0.74951035]]
[[ 0.23578994  6.864162    5.3911543  ... -0.07555743 -0.07555743
  -0.07555743]]
[[-0.1102102  23.490002   14.548181   ... -0.69032454 -0.69032454
  -0.69032454]]
[[-8.242773

In [3]:
from Recommenders.Hybrid.ItemUserHybridKNNRecommender import ItemUserHybridKNNRecommender
from Recommenders.KNN.ItemKNN_CFCBF_Hybrid_Recommender import ItemKNN_CFCBF_Hybrid_Recommender
URM_train, URM_test = split_train_in_two_percentage_global_sample(URM_csr, train_percentage=0.80)

evaluator_validation=EvaluatorHoldout(URM_test,cutoff_list=[10])
recommender_ItemKNNCFCBF = ItemUserHybridKNNRecommender(URM_train)
recommender_ItemKNNCFCBF.fit()

result_df, _ = evaluator_validation.evaluateRecommender(recommender_ItemKNNCFCBF)
result_df

EvaluatorHoldout: Ignoring 1566 ( 3.8%) Users that have less than 1 test interactions
ITEMCFCBF_ITEMKNNCF: URM Detected 3461 (12.4%) items with no interactions.
ItemKNNCFRecommender: URM Detected 3461 (12.4%) items with no interactions.
UserKNNCFRecommender: URM Detected 3461 (12.4%) items with no interactions.
Similarity column 27968 (100.0%), 2404.29 column/sec. Elapsed time 11.63 sec
Similarity column 41629 (100.0%), 1528.68 column/sec. Elapsed time 27.23 sec
[[-0.22624192  2.041109    4.0071144  ... -0.26737946 -0.26737946
  -0.26737946]
 [-0.21830659  1.201427    0.46382955 ... -0.26737946 -0.26737946
  -0.26737946]
 [ 1.169401    8.307266    7.973392   ... -0.26737946 -0.26737946
  -0.26737946]
 ...
 [ 0.40044022  4.1257215   2.8658717  ... -0.26737946 -0.26737946
  -0.26737946]
 [-0.1516939  -0.26737946 -0.26737946 ... -0.26737946 -0.26737946
  -0.26737946]
 [ 0.23713225  4.414356    2.9892635  ... -0.26737946 -0.26737946
  -0.26737946]]
[[-2.63508465e-02  1.22362261e+01  2.2742

/Users/fasa/PycharmProjects/RecSys-Challenge-2022-Polimi/Utils/metrics.py:276: RuntimeWarning: overflow encountered in power
  return np.sum(np.divide(np.power(2, scores) - 1, np.log2(np.arange(scores.shape[0], dtype=np.float64) + 2)),
/Users/fasa/PycharmProjects/RecSys-Challenge-2022-Polimi/Utils/metrics.py:270: RuntimeWarning: invalid value encountered in double_scalars
  ndcg_ = rank_dcg / ideal_dcg


[[-0.24383812  5.07447     1.9010568  ... -0.33043572 -0.33043572
  -0.33043572]
 [ 0.09230953  2.8509474   3.051913   ... -0.33043572 -0.33043572
  -0.33043572]
 [-0.16443294  2.2503252   1.529164   ... -0.33043572 -0.33043572
  -0.33043572]
 ...
 [-0.33043572 -0.33043572 -0.33043572 ... -0.33043572 -0.33043572
  -0.33043572]
 [-0.26073456 -0.33043572 -0.33043572 ... -0.33043572 -0.33043572
  -0.33043572]
 [ 0.24769135  5.524698    4.1466866  ... -0.33043572 -0.33043572
  -0.33043572]]
[[-0.02727508  1.2437285   0.13979527 ... -0.02727508 -0.02727508
  -0.02727508]
 [-0.02727508  2.7666905   1.604662   ... -0.02727508 -0.02727508
  -0.02727508]
 [-0.02727508 -0.02727508  0.01324373 ... -0.02727508 -0.02727508
  -0.02727508]
 ...
 [-0.02727508  0.18281312  0.05813963 ... -0.02727508 -0.02727508
  -0.02727508]
 [-0.02727508 -0.02727508 -0.02727508 ... -0.02727508 -0.02727508
  -0.02727508]
 [-0.02727508  2.2489882   2.5651     ... -0.02727508 -0.02727508
  -0.02727508]]
[[-0.35671768 -0

PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.050131                  0.08706  0.081783  0.025321    0.042926   

             MRR NDCG       F1  HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                  ...                 
10      0.164792  NaN  0.06216  0.324065      0.202437  ...      0.962382   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10              0.311874    0.962382       0.043274        9.562483   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                       0.993929             0.112211              0.725369   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                     3.271727      0.412391  

[1 rows x 27 columns]

In [4]:
from Recommenders.Hybrid.ItemUserHybridKNNRecommender import ItemUserHybridKNNRecommender
from Recommenders.KNN.ItemKNN_CFCBF_Hybrid_Recommender import ItemKNN_CFCBF_Hybrid_Recommender
URM_train, URM_test = split_train_in_two_percentage_global_sample(stacked_URM, train_percentage=0.80)

evaluator_validation=EvaluatorHoldout(URM_test,cutoff_list=[10])
recommender_ItemKNNCFCBF = ItemUserHybridKNNRecommender(URM_train)
recommender_ItemKNNCFCBF.fit()

result_df, _ = evaluator_validation.evaluateRecommender(recommender_ItemKNNCFCBF)
result_df

EvaluatorHoldout: Ignoring 1573 ( 3.8%) Users that have less than 1 test interactions
ITEMCFCBF_ITEMKNNCF: URM Detected 739 ( 2.6%) items with no interactions.
ItemKNNCFRecommender: URM Detected 739 ( 2.6%) items with no interactions.
UserKNNCFRecommender: URM Detected 739 ( 2.6%) items with no interactions.
Similarity column 27968 (100.0%), 3764.71 column/sec. Elapsed time 7.43 sec
Similarity column 41634 (100.0%), 1876.25 column/sec. Elapsed time 22.19 sec
[[-0.2563294   2.3300047   4.442718   ... -0.2563294  -0.2563294
  -0.2563294 ]
 [-0.2563294   1.1597202   0.42400455 ... -0.2563294  -0.2563294
  -0.2563294 ]
 [ 0.930565    8.00223     7.8246737  ... -0.2563294  -0.2563294
  -0.2563294 ]
 ...
 [-0.15604003 -0.2563294  -0.2563294  ... -0.2563294  -0.2563294
  -0.2563294 ]
 [ 0.02003297  4.972409    4.0288796  ... -0.2563294  -0.2563294
  -0.2563294 ]
 [-0.2563294  -0.2563294  -0.2563294  ... -0.2563294  -0.2563294
  -0.2563294 ]]
[[-2.6073890e-02  2.6323828e+01  2.4446118e+00 ... 

/Users/fasa/PycharmProjects/RecSys-Challenge-2022-Polimi/Utils/metrics.py:276: RuntimeWarning: overflow encountered in power
  return np.sum(np.divide(np.power(2, scores) - 1, np.log2(np.arange(scores.shape[0], dtype=np.float64) + 2)),


[[-0.3560541   8.92766     8.783985   ... -0.3560541  -0.3560541
  -0.3560541 ]
 [ 0.68627995  3.2419949   1.4362134  ... -0.3560541  -0.3560541
  -0.3560541 ]
 [ 0.06295637  8.271143    4.3637915  ... -0.3560541  -0.3560541
  -0.3560541 ]
 ...
 [ 0.08429351 48.280018   34.53944    ... -0.3560541  -0.3560541
  -0.3560541 ]
 [-0.3560541   1.93764     4.2270665  ... -0.3560541  -0.3560541
  -0.3560541 ]
 [-0.28966612  8.0835085   6.263029   ... -0.3560541  -0.3560541
  -0.3560541 ]]
[[-2.7860409e-02  7.8193913e+00  9.1240578e+00 ... -2.7860409e-02
  -2.7860409e-02 -2.7860409e-02]
 [ 3.1692091e-02  1.6775398e+00  1.0447487e+00 ... -2.7860409e-02
  -2.7860409e-02 -2.7860409e-02]
 [-1.0783718e-02  8.3644736e-01  2.0843171e-01 ... -2.7860409e-02
  -2.7860409e-02 -2.7860409e-02]
 ...
 [-2.7860409e-02  2.3120224e+01  4.9398472e+01 ... -2.7860409e-02
  -2.7860409e-02 -2.7860409e-02]
 [-2.7860409e-02  6.9029287e-02 -2.7860409e-02 ... -2.7860409e-02
  -2.7860409e-02 -2.7860409e-02]
 [-2.7860409e-

/Users/fasa/PycharmProjects/RecSys-Challenge-2022-Polimi/Utils/metrics.py:270: RuntimeWarning: invalid value encountered in double_scalars
  ndcg_ = rank_dcg / ideal_dcg


[[ 2.3517928   6.740098    6.338213   ... -0.3592819  -0.3592819
  -0.3592819 ]
 [-0.2356052   4.419127    5.3145947  ... -0.3592819  -0.3592819
  -0.3592819 ]
 [ 0.4427257   4.3102045   3.3071587  ... -0.3592819  -0.3592819
  -0.3592819 ]
 ...
 [-0.3592819   0.55262804  0.6707983  ... -0.3592819  -0.3592819
  -0.3592819 ]
 [ 0.60551536  5.592853    3.5833073  ... -0.3592819  -0.3592819
  -0.3592819 ]
 [-0.30617586  6.778789    2.9693522  ... -0.3592819  -0.3592819
  -0.3592819 ]]
[[ 0.02523409  0.23878174  0.33302212 ... -0.02649616 -0.02649616
  -0.02649616]
 [-0.02649616  0.13610072  0.04523933 ... -0.02649616 -0.02649616
  -0.02649616]
 [-0.02649616  3.479408    2.7733283  ... -0.02649616 -0.02649616
  -0.02649616]
 ...
 [-0.02649616  0.4638586   0.1271624  ... -0.02649616 -0.02649616
  -0.02649616]
 [-0.02649616  0.08932722  0.02024565 ... -0.02649616 -0.02649616
  -0.02649616]
 [-0.02649616  8.917636    3.7212608  ... -0.02649616 -0.02649616
  -0.02649616]]
[[-0.16120487 -0.08259

PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.050286                 0.087236  0.082095  0.025324    0.042546   

             MRR NDCG        F1  HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                   ...                 
10      0.165218  NaN  0.062369  0.325079      0.202974  ...      0.962218   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10              0.312797    0.962218       0.042852        9.559382   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                        0.99389             0.107317              0.721461   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                     3.259319      0.402513  

[1 rows x 27 columns]

In [5]:
from Recommenders.MatrixFactorization.IALSRecommender import IALSRecommender
URM_train, URM_test = split_train_in_two_percentage_global_sample(stacked_URM, train_percentage=0.80)

evaluator_validation=EvaluatorHoldout(URM_test,cutoff_list=[10])
recommender_ItemKNNCF = IALSRecommender(URM_train)
recommender_ItemKNNCF.fit()

result_df, _ = evaluator_validation.evaluateRecommender(recommender_ItemKNNCF)
result_df

IALSRecommender: URM Detected 684 ( 2.4%) items with no interactions.
IALSRecommender: Epoch 1 of 300. Elapsed time 10.69 sec
IALSRecommender: Epoch 2 of 300. Elapsed time 19.79 sec
IALSRecommender: Epoch 3 of 300. Elapsed time 29.30 sec
IALSRecommender: Epoch 4 of 300. Elapsed time 40.94 sec
IALSRecommender: Epoch 5 of 300. Elapsed time 50.41 sec
IALSRecommender: Epoch 6 of 300. Elapsed time 56.50 sec
IALSRecommender: Epoch 7 of 300. Elapsed time 1.05 min


KeyboardInterrupt: 